[![Open in Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/RizanSM/zero_shot_llms_in_HIL_RL/blob/main/01_Code/01_Highway_Env/03_Edge_Case_Scenario_1/02_BIASED_HF_DIRECT_AGG/01_Generate_trajectories_Biased_HF_D_Aggressive_Edge_Case_1.ipynb)

In [ ]:
# Install the required libraries in your Google Colab environment
!pip install stable-baselines3 gymnasium highway-env -q

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 184.5/184.5 kB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.0/105.0 kB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 77.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 63.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 36.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 82.1 MB/s eta 0:00:00


In [ ]:
# Import the necessary libraries
import gymnasium as gym
import highway_env
import numpy as np
import pandas as pd
import pickle
import os
import matplotlib.pyplot as plt

In [ ]:
from highway_env.road.road import Road, RoadNetwork, LaneIndex
from highway_env.vehicle.controller import ControlledVehicle
from highway_env.vehicle.kinematics import Vehicle

# EDGE CASE SCENARIO 1:
A custom wrapper for the Highway Environment implementing the following: <br>
    a. Ego vehicle: Starts in the rightmost lane (25 m/s)                <br>
    b. Set the rightmost lane as the lane with congestion (slower vehicles).<br>
    c. The adjacent lanes are populated with faster vehicles (speeds between 25-30 m/s).

In [ ]:
class VehicleGeneratorWrapper(gym.Wrapper):
    def __init__(self, env,traffic_lane_index, add_traffic, min_speed, max_speed, seed):
        """
        Wrapper for the highway environment to add new vehicles to a specific lane after reset.

        Parameters:
        env: The highway environment to be wrapped.
        lane_index: The index of the lane where ego vehicle will be spawned.
        traffic_lane_index: The index of the lane where vehicles will be added (0 to 3).
        add_traffic: Number of vehicles to be added to the lane.
        min_speed: Minimum speed (in m/s) of the new vehicles.
        max_speed: Maximum speed (in m/s) of the new vehicles.
        """
        super().__init__(env)

        self.seed_value = seed
        self.seed(self.seed_value)

        self.vehicles_count = env.unwrapped.config["vehicles_count"]
        self.lane_index = env.unwrapped.config["initial_lane_id"]
        self.traffic_lane_index = traffic_lane_index
        self.add_traffic = add_traffic
        self.min_speed = min_speed
        self.max_speed = max_speed
        self.added_vehicles = []  # Store added vehicles' details for display

    def seed(self, seed=None):
        # Update the seed value if provided
        if seed is not None:
            self.seed_value = seed

        # Seed Python's random module and NumPy's RNG
        np.random.seed(self.seed_value)

        # Return the seed(s) for consistency
        return [self.seed_value]

    def reset(self, **kwargs):

        self.seed(self.seed_value)

        """Reset the environment and add new vehicles to the specified lane."""
        obs, info = super().reset(seed=self.seed_value)
        # obs, info = super().reset()
        self._display_lane_traffic(before_reset=True)
        vehicle = self.env.unwrapped.vehicle
        target_lane_id = self.lane_index
        # target_lane_id_1 = self.traffic_lane_index

        # Log environment reset
        print(" Environment reset initiated")
        print(f" Ego vehicle starts in lane {target_lane_id} at speed 25 m/s")

        # a. Ego vehicle: Starts in the rightmost lane (25 m/s)
        self.ego_vehicle = ControlledVehicle(
            self.env.unwrapped.road,  # Changed from self.road
            vehicle.position,
            vehicle.heading,
            vehicle.speed,
            target_lane_index=target_lane_id,  # Ego Vehicle Starts in lane 3
            target_speed=25,  # Initial speed of ego vehicle = 25 m/s
        )
        self.vehicles = [self.ego_vehicle]

        # b. Set the rightmost lane as the lane with congestion (slower vehicles).
        self._add_vehicles()

        # c. The adjacent lanes are populated with faster vehicles (speeds between 25-30 m/s).
        self._set_lane_vehicle_speed([1, 2], 25, 30)  # Adjust speeds in Lane 1 and Lane 2
        self._display_lane_traffic(before_reset=False)

        # Display all vehicle details after reset
        print("All Vehicle details:")
        for v in self.env.unwrapped.road.vehicles:
            print(f"  Vehicle ID: {id(v)}, Lane: {v.lane_index[2]}, Position: {v.position}, Speed: {v.speed}")

        return obs, info

    def _add_vehicles(self):
        """Add vehicles to the specified lane in the environment."""
        self.added_vehicles = []  # Reset the list of added vehicles
        for i in range(self.add_traffic):
            lane = self.traffic_lane_index
            position = self._get_safe_position(lane)
            if position is None:
                print(f" Could not find a safe position for Vehicle {i + 1} in Lane {lane}")
                continue  # Skip adding this vehicle if no safe position is found

            speed = np.random.uniform(self.min_speed, self.max_speed)

            # Create and place the new vehicle
            new_vehicle = ControlledVehicle.create_random(
                self.env.unwrapped.road,
                lane_id=lane
            )
            new_vehicle.position = position  # Update with desired position
            new_vehicle.speed = speed
            self.env.unwrapped.road.vehicles.append(new_vehicle)

            # Store vehicle details for display
            self.added_vehicles.append({
                "id": i + 1,
                "position": position,
                "speed": speed})

            # DEBUGGING ADDED: Log added vehicle details
            print(f" Vehicle {i + 1} added to Lane {lane}: Position {position}, Speed {speed}")

    def _get_safe_position(self, lane):
        """Generate a safe longitudinal position for the new vehicle in the specified lane."""
        existing_vehicles = [v for v in self.env.unwrapped.road.vehicles if v.lane_index[2] == lane]
        existing_positions = [v.position[0] if isinstance(v.position, (list, np.ndarray)) else v.position for v in existing_vehicles]

        if not existing_positions:
            return 0  # Start of the lane if no vehicles exist

        max_retries = 100  # Maximum number of attempts to find a safe position
        for _ in range(max_retries):
            position = np.random.uniform(0, 500)  # Arbitrary range for position
            if all(abs(position - p) > 8 for p in existing_positions):  # Safe gap = 8
                return position

        # print("No valid position found after max retries")
        return None  # If no valid position is found after max_retries

    def _set_lane_vehicle_speed(self, lane_indices, min_speed_adj_lane, max_speed_adj_lane):
        """
        Set the speed of vehicles in specified lanes to be within the given range.

        Parameters:
        lane_indices: List of lane indices where vehicle speeds will be modified.
        min_speed: Minimum speed (in m/s) for vehicles in the specified lanes.
        max_speed: Maximum speed (in m/s) for vehicles in the specified lanes.
        """
        for lane in lane_indices:
            lane_vehicles = [v for v in self.env.unwrapped.road.vehicles if v.lane_index[2] == lane]
            for vehicle in lane_vehicles:
                vehicle.speed = np.random.uniform(min_speed_adj_lane, max_speed_adj_lane)

                # Log speed adjustments for vehicles
                print(f" Vehicle in Lane {lane} updated to Speed: {vehicle.speed:.2f} m/s")
            print("")

    def _display_lane_traffic(self, before_reset):
        """Display the number of vehicles in the specified lane and overall vehicle count."""
        lane_vehicles = [v for v in self.env.unwrapped.road.vehicles if v.lane_index[2] == self.lane_index]
        total_vehicles = len(self.env.unwrapped.road.vehicles)


        if before_reset:
            # print(f"Lane {self.lane_index} Vehicle Count before reset: {len(lane_vehicles)}")
            print(f"Total Vehicle Count before reset: {self.vehicles_count}")
        else:
            print(f"After reset: Number of vehicles added = {len(self.added_vehicles)}")
            for vehicle in self.added_vehicles:
                print(f"Vehicle added to Lane {self.lane_index}: Vehicle {vehicle['id']}: Position {vehicle['position']:.0f}, Speed {vehicle['speed']:.0f} m/s in Lane {self.lane_index}")
            #print(f"Lane {self.lane_index} Vehicle Count after reset: {len(lane_vehicles)}")
            print(f"Total Vehicle Count after reset: {total_vehicles}")
            print("")

    def log_episode_info(self, episode_info):
        """Log episode-specific information in the specified format."""
        for episode, info in episode_info.items():
            print(f"Episode {episode} Info: {info}")
        print("")  # Insert a blank line for better visibility

In [ ]:
# THE ENVIRONMENT
# Step 1.1: Choose the Environment
# Initialize the environment.
# First test : vehicles_count=50 , add_traffic=10
# Second test : vehicles_count=50 , add_traffic=5
env = gym.make("highway-v0")
env.unwrapped.config["vehicles_count"] = 50
env.unwrapped.config["initial_lane_id"] = 3
# Wrap the environment with different seed values
wrapped_env_1 = VehicleGeneratorWrapper(env, traffic_lane_index=3,add_traffic=10, min_speed=15, max_speed=20, seed=2)
wrapped_env_2 = VehicleGeneratorWrapper(env, traffic_lane_index=3, add_traffic=10, min_speed=15, max_speed=20, seed=10)
wrapped_env_3 = VehicleGeneratorWrapper(env, traffic_lane_index=3, add_traffic=10, min_speed=15, max_speed=20, seed=6)
wrapped_env_4 = VehicleGeneratorWrapper(env, traffic_lane_index=3, add_traffic=10, min_speed=15, max_speed=20, seed=20)
wrapped_env_5 = VehicleGeneratorWrapper(env, traffic_lane_index=3, add_traffic=10, min_speed=15, max_speed=20, seed=34)

Trajectory Collection with Additional information (Collision Flag and Lane Index)

In [ ]:
# TRAJECTORY COLLECTION WITH ADDTIONNAL INFORMATION
# Initialize a list to store trajectory data
trajectories = []

# FUNCTION TO COLLECT TRAJECTORY DATA (state-action-reward transitions).

def collect_trajectory_data(env, model, num_episodes):
    """
    Collect trajectory data for a number of episodes.
    Each trajectory contains state-action-reward sequences.
    """
    trajectory_data = []

    for episode in range(num_episodes):
        state, _ = env.reset()  # Reset the environment at the start of each episode              #  change environment name here
        done = False
        episode_data = []

        while not done:
            # Get action from the trained PPO model
            action, _states = model.predict(state, deterministic = True)                                       # change model name here

            # Take the action and get next state and reward
            next_state, reward, terminated, truncated, info = env.step(action)                    #  change environment name here
            done = terminated or truncated
            # Extract lane index and collision flag
            lane_index = int(env.unwrapped.vehicle.lane_index[2])
            collision_flag = int(info.get('crashed', 0))

            # Store the trajectory: (state, action, reward, next_state)
            episode_data.append({
                "state": state,
                "action": action,
                "reward": reward,
                "next_state": next_state,
                "lane_indices": lane_index,
                "collision_flags": collision_flag
            })

            # Update the state for the next iteration
            state = next_state

        # Add the episode data to the overall trajectory list
        trajectory_data.append(episode_data)

    return trajectory_data

In [ ]:
# FUNCTION TO PREPROCESS TRAJECTORY DATA
def preprocess_trajectory_data(trajectory_data):
    """
    Preprocesses the trajectory data into a structured format for further analysis.
    Returns a DataFrame with columns: episode, time_step, state, action, reward, next_state, speed, and reward_details.
    """
    processed_data = []

    for episode_num, episode_data in enumerate(trajectory_data):
        for time_step, step in enumerate(episode_data):
            # Flatten the state and next_state for easy interpretation (if they are multi-dimensional)
            state = np.array(step['state']).flatten()  # Flatten the state vector (if multi-dimensional)
            next_state = np.array(step['next_state']).flatten()  # Flatten the next_state vector

            collision_flag = step['collision_flags']
            lane_index = step['lane_indices']

            # Append the processed data for this step
            processed_data.append({
                "episode": episode_num,
                "time_step": time_step,
                "state": state,
                "action": step['action'],
                "reward": step['reward'],
                "next_state": next_state,
                "collision_flag": collision_flag,
                "lane_index": lane_index
            })

    # Convert the list of processed data into a DataFrame
    df = pd.DataFrame(processed_data)
    return df

In [ ]:
from stable_baselines3 import PPO
from google.colab import drive
from google.colab import data_table

# Mount Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


Model Loading

In [ ]:
# Step A.6.2: Load the all the saved PPO model
model = PPO.load('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/01_trained_models/3_ppo_highway_biased_hf_direct_aggressive')      # Update directory location 1

1. GENERATING TRAJECTORIES(BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1)



First BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1 data frame

In [ ]:
# Collect data for 100 episodes
trajectory_data_1 = collect_trajectory_data(wrapped_env_1, model, num_episodes=100)        # change environment and model name

Streaming output truncated to the last 5000 lines.
  Vehicle ID: 140303332826320, Lane: 2, Position: [302.43002852   8.        ], Speed: 25.81149299251157
  Vehicle ID: 140303332827216, Lane: 2, Position: [323.07744578   8.        ], Speed: 28.50376173303578
  Vehicle ID: 140303332824464, Lane: 3, Position: [344.75866287  12.        ], Speed: 22.412729656247272
  Vehicle ID: 140303332819536, Lane: 1, Position: [366.70880373   4.        ], Speed: 25.534728421549914
  Vehicle ID: 140303332831696, Lane: 0, Position: [388.8924107   0.       ], Speed: 23.547708970843303
  Vehicle ID: 140303332325136, Lane: 2, Position: [411.51554771   8.        ], Speed: 29.822755400446276
  Vehicle ID: 140303332316112, Lane: 2, Position: [433.64671715   8.        ], Speed: 27.500041805851083
  Vehicle ID: 140303332311952, Lane: 1, Position: [454.23736262   4.        ], Speed: 26.1015310353528
  Vehicle ID: 140303332319632, Lane: 1, Position: [473.01646868   4.        ], Speed: 26.749131425016497
  Vehicle 

/usr/local/lib/python3.11/dist-packages/highway_env/envs/common/observation.py:228: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[feature] = utils.lmap(df[feature], [f_range[0], f_range[1]], [-1, 1])
/usr/local/lib/python3.11/dist-packages/highway_env/envs/common/observation.py:230: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[feature] = np.clip(df[feature], -1, 1)
/usr/local/lib/python3.11/dist-packages/highway_env/envs/common/observation.py:228: SettingWithCopyWarning: 
A value is trying to be set 

Total Vehicle Count before reset: 50
 Environment reset initiated
 Ego vehicle starts in lane 3 at speed 25 m/s
 Vehicle 1 added to Lane 3: Position 217.99745107100188, Speed 15.129631159139457
 Vehicle 2 added to Lane 3: Position 274.8312389393546, Speed 17.176611963091386
 Vehicle 3 added to Lane 3: Position 165.16741050193707, Speed 16.02324317018921
 Vehicle 4 added to Lane 3: Position 309.63548317533184, Speed 16.498273368372615
 Vehicle 5 added to Lane 3: Position 133.4136375514333, Speed 18.105669163846475
 Vehicle 6 added to Lane 3: Position 264.57104713851953, Speed 15.672899726724667
 Vehicle 7 added to Lane 3: Position 92.21993282345764, Speed 18.926675739083368
 Vehicle 8 added to Lane 3: Position 426.9876463197444, Speed 17.47118418690964
 Vehicle 9 added to Lane 3: Position 39.8227385045305, Speed 17.52623045060852
 Vehicle 10 added to Lane 3: Position 48.26545783030628, Speed 15.635799858506388
 Vehicle in Lane 1 updated to Speed: 27.98 m/s
 Vehicle in Lane 1 updated to 

In [ ]:
# Preprocess the trajectory data
trajectory_df_1 = preprocess_trajectory_data(trajectory_data_1)

In [ ]:
data_table.enable_dataframe_formatter()
data_table.DataTable(trajectory_df_1)

In [ ]:
# Save the dataframe as a pickle file
trajectory_df_1.to_pickle('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/04_test_trajectories_edge_1/2_hf_d_aggressive_edge_1/1_trajectory_hf_d_aggressive_edge_1_df.pkl')           # change data frame name      # Update directory location 2

Second BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1 data frame

In [ ]:
# Collect data for 100 episodes
trajectory_data_2 = collect_trajectory_data(wrapped_env_2, model, num_episodes=100)        # change environment and model name

Streaming output truncated to the last 5000 lines.
Vehicle added to Lane 3: Vehicle 3: Position 112, Speed 16 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 4: Position 85, Speed 15 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 5: Position 343, Speed 20 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 6: Position 2, Speed 18 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 7: Position 406, Speed 18 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 8: Position 361, Speed 16 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 9: Position 459, Speed 19 m/s in Lane 3
Vehicle added to Lane 3: Vehicle 10: Position 271, Speed 16 m/s in Lane 3
Total Vehicle Count after reset: 61

All Vehicle details:
  Vehicle ID: 140303332839888, Lane: 3, Position: [183.62644474  12.        ], Speed: 25
  Vehicle ID: 140303297169552, Lane: 1, Position: [203.63969197   4.        ], Speed: 26.866703800257348
  Vehicle ID: 140303297170960, Lane: 0, Position: [224.66860477   0.        ], Speed: 21.40775881206152
  Vehicle I

In [ ]:
# Preprocess the trajectory data
trajectory_df_2 = preprocess_trajectory_data(trajectory_data_2)

In [ ]:
data_table.enable_dataframe_formatter()
data_table.DataTable(trajectory_df_2)

In [ ]:
# Save the dataframe as a pickle file
trajectory_df_2.to_pickle('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/04_test_trajectories_edge_1/2_hf_d_aggressive_edge_1/2_trajectory_hf_d_aggressive_edge_1_df.pkl')           # change data frame name    # Update directory location 3

Third BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1 data frame

In [ ]:
# Collect data for 100 episodes
trajectory_data_3 = collect_trajectory_data(wrapped_env_3, model, num_episodes=100)        # change environment and model name

Streaming output truncated to the last 5000 lines.
 Vehicle in Lane 1 updated to Speed: 27.70 m/s
 Vehicle in Lane 1 updated to Speed: 25.62 m/s
 Vehicle in Lane 1 updated to Speed: 29.79 m/s
 Vehicle in Lane 1 updated to Speed: 27.02 m/s
 Vehicle in Lane 1 updated to Speed: 26.08 m/s
 Vehicle in Lane 1 updated to Speed: 28.59 m/s
 Vehicle in Lane 1 updated to Speed: 29.97 m/s

 Vehicle in Lane 2 updated to Speed: 26.28 m/s
 Vehicle in Lane 2 updated to Speed: 28.36 m/s
 Vehicle in Lane 2 updated to Speed: 28.00 m/s
 Vehicle in Lane 2 updated to Speed: 28.59 m/s
 Vehicle in Lane 2 updated to Speed: 29.69 m/s
 Vehicle in Lane 2 updated to Speed: 26.76 m/s
 Vehicle in Lane 2 updated to Speed: 26.27 m/s
 Vehicle in Lane 2 updated to Speed: 27.01 m/s
 Vehicle in Lane 2 updated to Speed: 28.73 m/s
 Vehicle in Lane 2 updated to Speed: 28.62 m/s
 Vehicle in Lane 2 updated to Speed: 27.03 m/s
 Vehicle in Lane 2 updated to Speed: 29.95 m/s
 Vehicle in Lane 2 updated to Speed: 27.25 m/s
 Vehicle

In [ ]:
# Preprocess the trajectory data
trajectory_df_3 = preprocess_trajectory_data(trajectory_data_3)

In [ ]:
data_table.enable_dataframe_formatter()
data_table.DataTable(trajectory_df_3)

In [ ]:
# Save the dataframe as a pickle file
trajectory_df_3.to_pickle('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/04_test_trajectories_edge_1/2_hf_d_aggressive_edge_1/3_trajectory_hf_d_aggressive_edge_1_df.pkl')           # change data frame name    # Update directory location 4

Fourth BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1 data frame

In [ ]:
# Collect data for 100 episodes
trajectory_data_4 = collect_trajectory_data(wrapped_env_4, model, num_episodes=100)        # change environment and model name

Streaming output truncated to the last 5000 lines.
  Vehicle ID: 140303267424912, Lane: 3, Position: [859.96379412  12.        ], Speed: 22.897302149132887
  Vehicle ID: 140303267425104, Lane: 2, Position: [882.21779482   8.        ], Speed: 28.13426718858175
  Vehicle ID: 140303267425616, Lane: 2, Position: [901.86001068   8.        ], Speed: 27.787249052861412
  Vehicle ID: 140303267425808, Lane: 0, Position: [921.43460638   0.        ], Speed: 22.07699030749071
  Vehicle ID: 140303267425680, Lane: 3, Position: [943.88091347  12.        ], Speed: 22.183125735350522
  Vehicle ID: 140303267426384, Lane: 0, Position: [964.17103609   0.        ], Speed: 21.463645917704092
  Vehicle ID: 140303267421328, Lane: 2, Position: [986.45198943   8.        ], Speed: 26.59289779789901
  Vehicle ID: 140303267416592, Lane: 3, Position: [1007.03400323   12.        ], Speed: 21.556938041586314
  Vehicle ID: 140303267427536, Lane: 1, Position: [1029.77070482    4.        ], Speed: 28.25392957061665
  Ve

In [ ]:
# Preprocess the trajectory data
trajectory_df_4 = preprocess_trajectory_data(trajectory_data_4)

In [ ]:
data_table.enable_dataframe_formatter()
data_table.DataTable(trajectory_df_4)

In [ ]:
# Save the dataframe as a pickle file
trajectory_df_4.to_pickle('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/04_test_trajectories_edge_1/2_hf_d_aggressive_edge_1/4_trajectory_hf_d_aggressive_edge_1_df.pkl')           # change data frame name     # Update directory location 5

Fifth BIASED-HF-D-AGGRESSIVE-EDGE-CASE-1 data frame

In [ ]:
# Collect data for 100 episodes
trajectory_data_5 = collect_trajectory_data(wrapped_env_5, model, num_episodes=100)        # change environment and model name

Streaming output truncated to the last 5000 lines.
  Vehicle ID: 140303266432080, Lane: 3, Position: [302.76279985  12.        ], Speed: 23.77568626478321
  Vehicle ID: 140303266431952, Lane: 0, Position: [323.01692742   0.        ], Speed: 22.882486881266836
  Vehicle ID: 140303266433808, Lane: 2, Position: [344.4712733   8.       ], Speed: 29.671940802956865
  Vehicle ID: 140303266434896, Lane: 3, Position: [365.24276213  12.        ], Speed: 22.96477987745668
  Vehicle ID: 140303266434192, Lane: 0, Position: [385.24422556   0.        ], Speed: 22.4196700471074
  Vehicle ID: 140303266441360, Lane: 2, Position: [405.5177373   8.       ], Speed: 28.974059368521324
  Vehicle ID: 140303266439568, Lane: 2, Position: [425.96973127   8.        ], Speed: 27.307925510916494
  Vehicle ID: 140303266439696, Lane: 1, Position: [446.81712537   4.        ], Speed: 29.705733300283892
  Vehicle ID: 140303266440080, Lane: 1, Position: [468.11217598   4.        ], Speed: 25.40595337741398
  Vehicle ID:

In [ ]:
# Preprocess the trajectory data
trajectory_df_5 = preprocess_trajectory_data(trajectory_data_5)

In [ ]:
data_table.enable_dataframe_formatter()
data_table.DataTable(trajectory_df_5)

In [ ]:
# Save the dataframe as a pickle file
trajectory_df_5.to_pickle('/content/drive/MyDrive/05_zero_shot_llm_3/02_data/04_test_trajectories_edge_1/2_hf_d_aggressive_edge_1/5_trajectory_hf_d_aggressive_edge_1_df.pkl')          # Update directory location 6